In [50]:
import pandas as pd
import numpy as np
import plotly_express as px
from src.python.country_utils import country_utils
%load country_utils.py

ValueError: 'country_utils.py' was not found in history, as a file, url, nor in the user namespace.

In [43]:
df_train = pd.read_csv("E:/Skola/PycharmProjects/nn_covid-19_predictions/data/models/c19-week-4/train.csv", parse_dates=['Date'])
df_test = pd.read_csv("E:/Skola/PycharmProjects/nn_covid-19_predictions/data/models/c19-week-4/test.csv", parse_dates=['Date'])

df_test['Date'] = pd.to_datetime(df_test['Date'], format = '%Y-%m-%d')
df_train['Date'] = pd.to_datetime(df_train['Date'], format='%Y-%m-%d')

df_train.head()


Id Province_State Country_Region       Date  ConfirmedCases  Fatalities
0   1            NaN    Afghanistan 2020-01-22             0.0         0.0
1   2            NaN    Afghanistan 2020-01-23             0.0         0.0
2   3            NaN    Afghanistan 2020-01-24             0.0         0.0
3   4            NaN    Afghanistan 2020-01-25             0.0         0.0
4   5            NaN    Afghanistan 2020-01-26             0.0         0.0

In [44]:
df_tm = df_train.copy()
date = df_tm.Date.max()#get current date
df_tm = df_tm[df_tm['Date']==date]
obj = country_utils()

df_map = df_train.copy()
df_map['Date'] = df_map['Date'].astype(str)
df_map = df_map.groupby(['Date','Country_Region'], as_index=False)['ConfirmedCases','Fatalities'].sum()
df_map['iso_alpha'] = df_map.apply(lambda x: obj.fetch_iso3(x['Country_Region']), axis=1)
df_map['ln(ConfirmedCases)'] = np.log(df_map.ConfirmedCases + 1)
df_map['ln(Fatalities)'] = np.log(df_map.Fatalities + 1)

C:\Users\stefi\AppData\Roaming\Python\Python36\site-packages\ipykernel_launcher.py:8: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



In [45]:
# Vypis mapy
# Vypis pripadov podla dni
px.choropleth(df_map, 
              locations="iso_alpha", 
              color="ln(ConfirmedCases)", 
              hover_name="Country_Region", 
              hover_data=["ConfirmedCases"] ,
              animation_frame="Date",
              color_continuous_scale=px.colors.sequential.dense, 
              title='Celkové potvrdené prípady nákazy vo svete (podľa dní)')

In [46]:
px.choropleth(df_map, 
              locations="iso_alpha", 
              color="ln(Fatalities)", 
              hover_name="Country_Region",
              hover_data=["Fatalities"],
              animation_frame="Date",
              color_continuous_scale=px.colors.sequential.OrRd,
              title = 'Celkový nárast úmrtí (podľa dní)')


In [47]:
# Umrtnost v %
df_map['Mortality Rate%'] = round((df_map.Fatalities/df_map.ConfirmedCases)*100,2)

In [48]:
px.choropleth(df_map, 
                    locations="iso_alpha", 
                    color="Mortality Rate%", 
                    hover_name="Country_Region",
                    hover_data=["ConfirmedCases","Fatalities"],
                    animation_frame="Date",
                    color_continuous_scale=px.colors.sequential.Magma_r,
                    title = 'Celosvetová denná zmena úmrtnosti v %')
